# cPEPmatch

In [30]:
CREATE_CYCLOLIB=1
CREATE_INTERFACES=1
PROCESS_INTERFACE=1
FIND_MATCH=1

In [31]:
interface_cutoff=7
motif_size=4
frmsd_threshold=0.7

In [61]:
import sys,os,re, glob
import operator #set of efficient functions
import pickle #store data on disc
import time
import warnings
import numpy as np
import shutil #import copyfile

os.environ["STRIDE_BIN"]='/home/brianda/usr/local/bin/stride'

from scipy import spatial
from glob import glob
from collections import defaultdict
from itertools import product
from cycler import cycler
from sys import exit
from modeller import *
from modeller.optimizers import MolecularDynamics, ConjugateGradients
from modeller.automodel import autosched

import Bio
from Bio.PDB import PDBParser
from Bio.PDB.parse_pdb_header import parse_pdb_header

import vmd
from vmd import molecule, atomsel

os.chdir('/home/brianda/Documents/cPEPmatch/example_match/')

## 1. Cyclo Library

This section characterizes the cyclic peptide motifs.

In [51]:
def int_list(lyst, sep=' ', quote=None):
    """Return the list of numbers in 'lyst' as a string separated by 'sep'."""
    f = str if quote is None else lambda i: quote+str(i)+quote
    return sep.join(map(f, lyst))

def cyclo_distance_matrix(nres, R, fname):
    M = dict()
    
    for i,res in enumerate(R[:-nres+1]):
        #print(res, res+nres, R[i:i+nres])
        resids = R[i:i+nres]
        if not np.all(np.diff(resids)==1): continue
        rlist = int_list(resids, quote='"')
        #if not rnbrs: continue
        QA = '''(chain M and name CA and (altloc "A" or altloc "") and resid %(rlist)s)'''
        QA = ' '.join(str(QA).split())
        
        resid_query = atomsel(QA % dict(rlist=rlist))
        r = np.array(resid_query.centerperresidue())
        
        #
        # Ignore sequences that are either near the ends of a chain, or are near ends of a broken chain
        #
        if len(r) != nres: continue
        assert len(r) == nres, (len(r), r, nres, res, rnbrs, resid_query, fname)
        
        dr = spatial.distance_matrix(r,r)
        m = dr[np.triu_indices(nres,k=2)]
        M[resids[0]] = dict(
            m=m,
#            r=r,
            resid=resids,
        )
    return M




def cyclo_motifs(molid):
    C = atomsel('chain M and protein and backbone and (altloc "A" or altloc "") ')
    C_res = list(sorted(set(C.resid)))
    MC = cyclo_distance_matrix(motif_size, C_res, cyclo)
    
    return (MC)

In [52]:
if CREATE_CYCLOLIB:
    #os.chdir(cwd + "/cyclo_library")
    os.chdir('/home/brianda/Documents/cpep/cyclo_library/')

    parser = PDBParser()
    cyclo_mtfs = []
    
    #All cyclic peptides, including those with non-standard amino acids.
    #lib = ['2c9t', '1cnl', '1tk2', '5eoc', '3zwz', '4z0f', '4zjx', '4ib5', '3oe0', '6c1r', '1urc', '4w4z', 
          # '1ebp', '3pqz', '3avb', '4n7y', '5xco', '4k8y', '1jbl', '3p8f', '4i80', '5afg', '3wbn', '1npo', 
          # '2mgo', '3wmg', '5kgn', '5b4w', '5lso', '5xn3', '1sld', '5bxo', '4zqw', '4ktu', '4kts', '4twt', 
          # '3qn7', '3av9', '3ava', '3avi', '3wnf', '1sle', '1vwb', '5n99', '4os1', '4mnw', '4jk5', '4gly', 
          # '4x1n', '5glh', '2m2g', '2lwv', '6pip', '2lwt', '1foz', '2ajw', '5lff', '2ox2', '6axi', '2lwu', 
          # '3wne', '2ak0', '2lws', '1qx9', '6pin', '2n07', '1l5g', '6pio', '2jrw', '6awm', '5vav', '6awk' ]
    
    #Only cyclic peptides with standard amino acids.
    lib = ['1cnl', '1ebp', '1foz', '1jbl', '1l5g', '1npo', '1qx9', '1sld', '1sle', '1urc', '1vwb', '2ajw', 
           '2ak0', '2c9t', '2jrw', '2lws', '2lwt', '2lwu', '2lwv', '2m2g', '2mgo', '2n07', '2ox2', '3av9', 
           '3ava', '3avb', '3avi', '3p8f', '3wbn', '3wne', '3wnf', '3zwz', '4gly', '4ib5', '4jk5', 
           '4k8y', '4kts', '4ktu', '4mnw', '4mq9', '4twt', '4x1n', '5bxo', '5eoc', '5glh', '5lff', '5lso', 
           '5vav', '5xco', '5xn3', '6awk', '6awm', '6axi', '6pin', '6pio', '6pip' ]

   
    
    for c in lib:
        motifs = dict()
        cyclo = ('%s-cp.pdb' % c)
        molid = molecule.load("pdb", cyclo )
        c_mtfs = cyclo_motifs(molid)
        if c_mtfs is not None:
            #save_interacting_sidechains(os.path.splitext(f)[0], isc)
            motifs.update({c: c_mtfs})
            cyclo_mtfs.append(motifs)
cyclo_mtfs


[{'1cnl': {1: {'m': array([5.73403453, 4.78332382, 5.27912862]),
    'resid': [1, 2, 3, 4]},
   2: {'m': array([5.27912862, 5.82264682, 4.88279656]),
    'resid': [2, 3, 4, 5]},
   3: {'m': array([4.88279656, 5.44200798, 6.46273336]),
    'resid': [3, 4, 5, 6]},
   4: {'m': array([6.46273336, 8.31122035, 5.37896318]),
    'resid': [4, 5, 6, 7]},
   5: {'m': array([5.37896318, 6.54750527, 5.11513158]),
    'resid': [5, 6, 7, 8]},
   6: {'m': array([5.11513158, 4.46125902, 6.00003041]),
    'resid': [6, 7, 8, 9]},
   7: {'m': array([6.00003041, 9.07639155, 5.65425667]),
    'resid': [7, 8, 9, 10]},
   8: {'m': array([5.65425667, 8.55130383, 5.48538493]),
    'resid': [8, 9, 10, 11]},
   9: {'m': array([5.48538493, 6.55884076, 5.29608133]),
    'resid': [9, 10, 11, 12]}}},
 {'1ebp': {1: {'m': array([7.01840431, 9.7657373 , 6.35382789]),
    'resid': [1, 2, 3, 4]},
   2: {'m': array([ 6.35382789, 10.093343  ,  7.19687447]),
    'resid': [2, 3, 4, 5]},
   3: {'m': array([ 7.19687447, 10.731

## 2. PPI

This section selects the residues of the PPI interface and characterizes its CA motifs. 
Name the PPI input file as 'complex.pdb'

### 2.1 Interface 

In [53]:
def interfaces(molid, cutoff=interface_cutoff, minresidues=4):

    Iall = []
    tag = 'pp'
    chains = [['A'], ['B']] #TODO:read chains from the pdb
    for a,b in product(*chains): # gets all possible combination-pairs of chains.
        if a == b: continue
        Qa = 'protein and noh and chain %(A)s and same residue as exwithin %(cutoff)f of chain %(B)s'
        Qb = 'protein and noh and chain %(B)s and same residue as exwithin %(cutoff)f of chain %(A)s'
        Ia = atomsel(Qa % dict(A=a, B=b, cutoff=cutoff))
        Ib = atomsel(Qb % dict(A=a, B=b, cutoff=cutoff))
        if len(set(Ia.residue)) < minresidues: continue
        if len(set(Ib.residue)) < minresidues: continue
        #I = atomsel(('(%s) or (%s)' % (Qa,Qb)) % dict(A=a, B=b, cutoff=cutoff))
        I = atomsel(Qb % dict(A=a, B=b, cutoff=cutoff))
        Iall.append( (a,b,I,tag) )
    return Iall


def create_interfaces(): 
    parser = PDBParser()
    pdb_fname = 'complex.pdb'
    try:
        molid  = molecule.load("pdb", pdb_fname) #from vmd library 
        Iall = interfaces(molid) 
        
        for a,b,I,tag in Iall:
            int_fname = 'interface.pdb'
            print('%s -> %s' % (pdb_fname, int_fname))
            molecule.write(molid, 'pdb', int_fname, selection=I)
        molecule.delete(molid)
    except RuntimeError as e:
        warn(e)
        pass


In [54]:
if CREATE_INTERFACES:
    os.chdir('/home/brianda/Documents/cPEPmatch/example_match/')
    create_interfaces()

complex.pdb -> interface.pdb


### 2.1 Motif construction

In [55]:
def int_list(lyst, sep=' ', quote=None):
    """Return the list of numbers in 'lyst' as a string separated by 'sep'."""
    f = str if quote is None else lambda i: quote+str(i)+quote
    return sep.join(map(f, lyst))

def load_interface(pdb_fname): # process_all_interfaces(load_interface,...)
    """Return a vmd molecule for the interface found in pdb_fname in a tuple of (vmd-mol, pdb-code, tag, list-of-chains)."""
    d,f = os.path.split(pdb_fname) # d = path/.../, f = x.pdb
    pdb,tag,chains,ext = f.split('.') # e.g. 4gko, pp, B-G, pdb
    chains = chains.split('-')
    mol = molecule.load("pdb", pdb_fname) # What is molecule in that context? 
    #vmd.render.render('PostScript', pdb_fname + '.ps')
    #molecule.ssrecalc(int(mol)) # recalculate secondary structure
    return (mol, pdb, tag, chains) # (12, '4gko', 'pp', ['D', 'J'])


def distance_matrix(nres, chain, R, fname):
    M = dict()
    for i,res in enumerate(R[:-nres+1]):
        #print(res, res+nres, R[i:i+nres])
        resids = R[i:i+nres]
        if not np.all(np.diff(resids)==1): continue
        rlist = int_list(resids, quote='"')
        #if not rnbrs: continue
        QB = '''(chain %(chainB)s and name CA and (altloc "A" or altloc "") and resid %(rlist)s)'''
        QB = ' '.join(str(QB).split())
        
        resid_query = atomsel(QB % dict(chainB=chain, rlist=rlist))
        clz = resid_query.structure
        r = np.array(resid_query.centerperresidue())
        
        #
        # Ignore sequences that are either near the ends of a chain, or are near ends of a broken chain
        #
        if len(r) != nres: continue
        assert len(r) == nres, (len(r), r, nres, res, rnbrs, resid_query, fname)
        
        dr = spatial.distance_matrix(r,r)
        m = dr[np.triu_indices(nres,k=2)]
        M[resids[0]] = dict(
            m=m,
#            r=r,
            resid=resids,
        )
    return M

        
def motifs(molid, v=0):
    chainA,chainB = ['A', 'B'] #TODO choose the chain
    B = atomsel('protein and chain %s and backbone and (altloc "A" or altloc "") ' % chainB)
    B_res = list(sorted(set(B.resid)))
    MB = distance_matrix(motif_size, chainB, B_res, inter_fname)
    return (MB)


In [56]:
if PROCESS_INTERFACE:
    os.chdir('/home/brianda/Documents/cPEPmatch/example_match/')
    parser = PDBParser()
    inter_fname = "interface.pdb"
    molid  = molecule.load("pdb", inter_fname)
    mtfs = motifs(molid)
    
mtfs

{10: {'m': array([5.48921817, 9.20551311, 6.92821609]),
  'resid': [10, 11, 12, 13]},
 11: {'m': array([6.92821609, 7.90129135, 5.85215546]),
  'resid': [11, 12, 13, 14]},
 12: {'m': array([5.85215546, 8.24990213, 6.54848125]),
  'resid': [12, 13, 14, 15]},
 13: {'m': array([6.54848125, 9.33086217, 6.06756605]),
  'resid': [13, 14, 15, 16]},
 14: {'m': array([6.06756605, 8.81588553, 6.5201691 ]),
  'resid': [14, 15, 16, 17]},
 15: {'m': array([6.5201691 , 9.18589432, 6.07416577]),
  'resid': [15, 16, 17, 18]},
 16: {'m': array([6.07416577, 9.70161094, 6.68805018]),
  'resid': [16, 17, 18, 19]},
 17: {'m': array([6.68805018, 9.49226684, 6.35796707]),
  'resid': [17, 18, 19, 20]},
 34: {'m': array([6.46773765, 9.08297252, 5.64330574]),
  'resid': [34, 35, 36, 37]},
 35: {'m': array([5.64330574, 7.82443628, 6.05089822]),
  'resid': [35, 36, 37, 38]},
 36: {'m': array([6.05089822, 8.46553468, 7.22055502]),
  'resid': [36, 37, 38, 39]},
 37: {'m': array([7.22055502, 7.53155585, 5.66629113])

## 3. Backbone Match

This section matches the CA distance motifs of the PPI and the cyclic peptide database.

In [57]:
MOTIF4 = 4

if FIND_MATCH:
    match = dict()
    all_match = []
    matches = []
    for pp in mtfs:
        if motif_size == MOTIF4:
            d_ppi = [(mtfs[pp]["m"][0]),(mtfs[pp]["m"][1]),(mtfs[pp]["m"][2])]
            ms=3
        else:
            d_ppi = [(mtfs[pp]["m"][0]),(mtfs[pp]["m"][1]),(mtfs[pp]["m"][2]),(mtfs[pp]["m"][3]),(mtfs[pp]["m"][4]),(mtfs[pp]["m"][5])]
            ms=6
        for i in range(0,31):
            for c in cyclo_mtfs[i]:
                peptide = c
                for d in (cyclo_mtfs[i][c]):
                    if motif_size == MOTIF4:
                        d_cyclo = [(cyclo_mtfs[i][c][d]["m"][0]),(cyclo_mtfs[i][c][d]["m"][1]),(cyclo_mtfs[i][c][d]["m"][2])]
                    else:
                        d_cyclo = [(cyclo_mtfs[i][c][d]["m"][0]),(cyclo_mtfs[i][c][d]["m"][1]),(cyclo_mtfs[i][c][d]["m"][2]),(cyclo_mtfs[i][c][d]["m"][3]),(cyclo_mtfs[i][c][d]["m"][4]),(cyclo_mtfs[i][c][d]["m"][5])]
                    sum = 0
                    for r in range(0, ms):
                        dd = (d_ppi[r]-d_cyclo[r])**2
                        sum = sum + dd
                    rmsd = np.sqrt(sum)
                    if rmsd < frmsd_threshold:
                        rmsd = rmsd.round(decimals=4)
                        match = ( peptide , rmsd,  cyclo_mtfs[i][c][d]["resid"], mtfs[pp]["resid"] )
                        all_match.append(match)                       

all_match.sort()
all_match


[('1cnl', 0.4679, [7, 8, 9, 10], [34, 35, 36, 37]),
 ('1cnl', 0.6774, [7, 8, 9, 10], [15, 16, 17, 18]),
 ('1ebp', 0.1755, [5, 6, 7, 8], [16, 17, 18, 19]),
 ('1ebp', 0.1847, [8, 9, 10, 11], [36, 37, 38, 39]),
 ('1ebp', 0.2295, [10, 11, 12, 13], [13, 14, 15, 16]),
 ('1ebp', 0.3429, [11, 12, 13, 14], [16, 17, 18, 19]),
 ('1ebp', 0.3541, [10, 11, 12, 13], [15, 16, 17, 18]),
 ('1ebp', 0.4289, [1, 2, 3, 4], [17, 18, 19, 20]),
 ('1ebp', 0.4477, [10, 11, 12, 13], [17, 18, 19, 20]),
 ('1ebp', 0.4526, [6, 7, 8, 9], [11, 12, 13, 14]),
 ('1ebp', 0.4677, [13, 14, 15, 16], [17, 18, 19, 20]),
 ('1ebp', 0.5094, [10, 11, 12, 13], [34, 35, 36, 37]),
 ('1ebp', 0.5646, [13, 14, 15, 16], [15, 16, 17, 18]),
 ('1ebp', 0.57, [4, 5, 6, 7], [15, 16, 17, 18]),
 ('1ebp', 0.5772, [13, 14, 15, 16], [13, 14, 15, 16]),
 ('1ebp', 0.6212, [11, 12, 13, 14], [10, 11, 12, 13]),
 ('1ebp', 0.6329, [6, 7, 8, 9], [37, 38, 39, 40]),
 ('1ebp', 0.6377, [4, 5, 6, 7], [13, 14, 15, 16]),
 ('1ebp', 0.6963, [4, 5, 6, 7], [17, 18, 19,

## 4. Superimpose & Mutate

This section superimposes the matched structures. Output files are the superimposed pdb's and a full list of the matches.

In [58]:
#MODELLER optimization

def optimize(atmsel, sched):
    #conjugate gradient
    for step in sched:
        step.optimize(atmsel, max_iterations=200, min_atom_shift=0.001)
    #md
    refine(atmsel)
    cg = ConjugateGradients()
    cg.optimize(atmsel, max_iterations=200, min_atom_shift=0.001)


#molecular dynamics
def refine(atmsel):
    # at T=1000, max_atom_shift for 4fs is cca 0.15 A.
    md = MolecularDynamics(cap_atom_shift=0.39, md_time_step=4.0,
                           md_return='FINAL')
    init_vel = True
    for (its, equil, temps) in ((200, 20, (150.0, 250.0, 400.0, 700.0, 1000.0)),
                                (200, 600,
                                 (1000.0, 800.0, 600.0, 500.0, 400.0, 300.0))):
        for temp in temps:
            md.optimize(atmsel, init_velocities=init_vel, temperature=temp,
                         max_iterations=its, equilibrate=equil)
            init_vel = False


#use homologs and dihedral library for dihedral angle restraints
def make_restraints(mdl1, aln):
   rsr = mdl1.restraints
   rsr.clear()
   s = Selection(mdl1)
   for typ in ('stereo', 'phi-psi_binormal'):
       rsr.make(s, restraint_type=typ, aln=aln, spline_on_site=True)
   for typ in ('omega', 'chi1', 'chi2', 'chi3', 'chi4'):
       rsr.make(s, restraint_type=typ+'_dihedral', spline_range=4.0,
                spline_dx=0.3, spline_min_points = 5, aln=aln,
                spline_on_site=True)
    
    
    
def overlap_finder(match_path, complex_fname, matched_sequence):
    
    parser = PDBParser()
    ppi = molecule.load("pdb", complex_fname)    
    receptor_chain = atomsel('chain A') #change this if the receptor has a different chain name.
    #receptor_chain = ' '.join(str(receptor_chain).split())
    
    parser = PDBParser()
    cyclo = molecule.load("pdb", (match_path + 'cpep_aligned.pdb'))
    cyclo_chain = atomsel('chain M and not resid {}'.format(matched_sequence))
    #cyclo_chain = ' '.join(str(cyclo_chain).split())
    
    overlap = atomsel.contacts(cyclo_chain, receptor_chain, 1)
    
    return overlap         

In [71]:
#TODO: Adapt a 5-motif superimposition and mutation

os.chdir('/home/brianda/Documents/cPEPmatch/example_match/')
#cwd = '/home/brianda/Documents/cPEPmatch/example_match/'

#Delete old match files 
dir = [os.listdir('.')]
for f in dir:
    for a in f:
        if "match" in a:
            try:
                os.remove(a)
            except OSError as e:
                 pass
                    
                    

match_directory_list = []
all_mutations = dict()

cr = 1
c1 = 1
real_match_count = 1

with open('match_list.txt', 'w') as f:
    f.write("List of matches found by cPEPmatch.\nMotif Size: {} \nInterface Cutoff: {} \nFit-RMSD Threshold: {} \n\n" .format(motif_size, interface_cutoff,frmsd_threshold))
    f.write(" Match  pdb   Dist-RMSD    CPep Residues        PP-Interface Residues   Fit-RMSD\n\n")

    for match in all_match: 
        
        no_overlap_match = []
    
        pdb_parser = Bio.PDB.PDBParser(QUIET = True)
        matched_cyclopep = match[0]
        match_dir = ("match{}_{}".format(cr, matched_cyclopep))
        match_directory_list.append(match_dir)
    
        
        #Selection of residues to be aligned
    
        cyclo_start_id = match[2][0]
        cyclo_end_id = match[2][3]
        cyclo_residues_to_be_aligned = range(cyclo_start_id, (cyclo_end_id + 1))
    
        ppi_start_id = match[3][0]
        ppi_end_id = match[3][3]
        ppi_residues_to_be_aligned = range(ppi_start_id, (ppi_end_id + 1))
    
    
        #Create a directory for each match
    
        try:
            os.mkdir("{}".format(match_dir))
            cr  =  cr + 1
        except:
            print("Match folder already exist")
    
        #cpep = (cwd + ('/cyclo_library/{}-cp.pdb'.format(matched_cyclopep)))
        cpep = ('/home/brianda/Documents/cpep/cyclo_library/{}-cp.pdb'.format(matched_cyclopep))
        match_folder = (cwd + ('/{}/cpep_match.pdb'.format(match_dir)))
        match_path = (cwd + ('/{}/'.format(match_dir)))

        try:
            #os.popen('cp {} {}'.format(cpep, os.path.join(match_folder, filename)))
            #copyfile(cpep, match_folder)
            shutil.copy(cpep, match_folder, follow_symlinks=True)
            
        except IOError as e:
            print("Unable to copy file. %s" % e)
            
        
        # Get the structures
        cyclo_structure = pdb_parser.get_structure("reference", (cwd + ("/{}/cpep_match.pdb".format(match_dir))))  
        ppi_structure = pdb_parser.get_structure("sample", (cwd + "/interface.pdb"))

        cyclo_model = cyclo_structure[0]
        cyclo_chain = cyclo_model['M']
        ppi_model = ppi_structure[0]
        ppi_chain = ppi_model['B']
        

        # List of atoms to align.
        cyclo_atoms = []
        ppi_atoms = []

        for cyclo_chain in cyclo_model:
            for cyclo_res in cyclo_chain:
                if cyclo_res.get_id()[1] in cyclo_residues_to_be_aligned: # Check if residue number ( .get_id() ) is in the list
                    cyclo_atoms.append(cyclo_res['CA'])

        
        for ppi_chain in ppi_model:
            for ppi_res in ppi_chain:
                if ppi_res.get_id()[1] in ppi_residues_to_be_aligned:
                    ppi_atoms.append(ppi_res['CA'])
        
        # Superimposer:
        super_imposer = Bio.PDB.Superimposer()
        super_imposer.set_atoms(ppi_atoms, cyclo_atoms)
        super_imposer.apply(cyclo_model.get_atoms())

        # Add to fit_RMSD the results:
        superimpose_rmsd = super_imposer.rms
        lst = list(match)
        lst = lst + [superimpose_rmsd]
        match = tuple(lst)
    
        # Save the aligned version 
        io = Bio.PDB.PDBIO()
        io.set_structure(cyclo_structure) 
        io.save(match_path + "cpep_aligned.pdb") 
        
        
        #Eliminates the matched cyclic peptides that overlap with the receptor. 
        
        matched_cyclo_residues = (str(cyclo_start_id) + ' to ' + str(cyclo_end_id))
        overlap = overlap_finder(match_path, (cwd + "/complex.pdb"), matched_cyclo_residues)

        if overlap == [[],[]]:
            no_overlap_match = match
        
        
        #WRITE OUTPUT FILE
        if no_overlap_match != []:
            c2 = 0
            f.write("{:>6}".format(c1))
            for i in no_overlap_match:
                if c2 < 1:
                    f.write("{:>6} ".format(i))
                elif c2 < 2:
                    f.write("{:>9.4f}".format(i))
                elif c2 < 3:
                    f.write("   ")
                    for r in i:
                        f.write("{:>5}".format(r))
                elif c2 < 4:
                    f.write("   ")
                    for r in i:
                        f.write("{:>5}".format(r))
                else:
                    f.write("   ")
                    f.write("{:>9.4f}".format(i))

                c2 = c2 + 1

            f.write("\n")
            c1 = c1 + 1  

    
    
            #MUTATE

            modelname = (match_path + 'cpep_aligned.pdb') 
            motif_length = len(match[2]) - 1
            mutation_count = 0

            for matched_residue in range (match[2][0], (match[2][motif_length] + 1)):

                respos = str(matched_residue)
                residue_number_to_match = match[3][mutation_count]
                restyp = ppi_chain[residue_number_to_match].get_resname()     
                cyclic_restyp = cyclo_chain[matched_residue].get_resname()
                chain = 'M'
                disulfide = 'CYX'

                if cyclic_restyp != disulfide:
                    
                    try:
                        log.verbose()

                        # Set a different value for rand_seed to get a different final model
                        env = Environ(rand_seed=-49837)

                        env.io.hetatm = True
                        #soft sphere potential
                        env.edat.dynamic_sphere=False
                        #lennard-jones potential (more accurate)
                        env.edat.dynamic_lennard=True
                        env.edat.contact_shell = 4.0
                        env.edat.update_dynamic = 0.39

                        # Read customized topology file with phosphoserines (or standard one)
                        env.libs.topology.read(file='$(LIB)/top_heav.lib')

                        # Read customized CHARMM parameter library with phosphoserines (or standard one)
                        env.libs.parameters.read(file='$(LIB)/par.lib')


                        # Read the original PDB file and copy its sequence to the alignment array:
                        mdl1 = Model(env, file=modelname)
                        ali = Alignment(env)
                        ali.append_model(mdl1, atom_files=modelname, align_codes=modelname)

                        #set up the mutate residue selection segment
                        s = Selection(mdl1.chains[chain].residues[respos])

                        #perform the mutate residue operation
                        s.mutate(residue_type=restyp)
                        #get two copies of the sequence.  A modeller trick to get things set up
                        ali.append_model(mdl1, align_codes=modelname)

                        # Generate molecular topology for mutant
                        mdl1.clear_topology()
                        mdl1.generate_topology(ali[-1])


                        # Transfer all the coordinates you can from the template native structure
                        # to the mutant (this works even if the order of atoms in the native PDB
                        # file is not standard):
                        #here we are generating the model by reading the template coordinates
                        mdl1.transfer_xyz(ali)

                        # Build the remaining unknown coordinates
                        mdl1.build(initialize_xyz=False, build_method='INTERNAL_COORDINATES')

                        #yes model2 is the same file as model1.  It's a modeller trick.
                        mdl2 = Model(env, file=modelname)

                        #required to do a transfer_res_numb
                        #ali.append_model(mdl2, atom_files=modelname, align_codes=modelname)
                        #transfers from "model 2" to "model 1"
                        mdl1.res_num_from(mdl2,ali)

                        #It is usually necessary to write the mutated sequence out and read it in
                        #before proceeding, because not all sequence related information about MODEL
                        #is changed by this command (e.g., internal coordinates, charges, and atom
                        #types and radii are not updated).

                        mdl1.write(file=modelname+restyp+respos+'.tmp')
                        mdl1.read(file=modelname+restyp+respos+'.tmp')

                        #set up restraints before computing energy
                        #we do this a second time because the model has been written out and read in,
                        #clearing the previously set restraints
                        make_restraints(mdl1, ali)

                        #a non-bonded pair has to have at least as many selected atoms
                        mdl1.env.edat.nonbonded_sel_atoms=1

                        sched = autosched.loop.make_for_model(mdl1)

                        #only optimize the selected residue (in first pass, just atoms in selected
                        #residue, in second pass, include nonbonded neighboring atoms)
                        #set up the mutate residue selection segment
                        s = Selection(mdl1.chains[chain].residues[respos])

                        mdl1.restraints.unpick_all()
                        mdl1.restraints.pick(s)

                        s.energy()

                        s.randomize_xyz(deviation=4.0)

                        mdl1.env.edat.nonbonded_sel_atoms=2
                        optimize(s, sched)

                        #feels environment (energy computed on pairs that have at least one member
                        #in the selected)
                        mdl1.env.edat.nonbonded_sel_atoms=1
                        optimize(s, sched)

                        s.energy()

                        #Output file
                        #mdl1.write(file=modelname+restyp+respos+'.pdb')
                        mdl1.write(match_path + ('mutation{}.pdb'.format(mutation_count)))

                        #delete the temporary file
                        os.remove(modelname+restyp+respos+'.tmp')

                        shutil.copyfile((match_path + ('mutation{}.pdb'.format(mutation_count))), (match_path + ('mutated_match.pdb')))
                        modelname = (match_path + ('mutated_match.pdb'))

                        mutation_count = mutation_count + 1
                    
                    
                    except RuntimeError as e:
                        print('Non-standard amino acid found in the cyclic peptide sequence {}.'
                              ' I will not be mutated'.format(matched_cyclopep))
                        pass

                else:
                    mutation_count = mutation_count + 1
            
            
            shutil.copyfile((match_path + ('mutated_match.pdb')), 
                            ('match{}_{}.pdb'.format(real_match_count, matched_cyclopep)))
            real_match_count = real_match_count + 1
            
        
            for fname in os.listdir(match_path):
                if fname.startswith("mutation"):
                    os.remove(os.path.join(match_path, fname))
            
            shutil.rmtree(match_dir)    
            
            
        else:
            shutil.rmtree(match_dir)


                


openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           ${MODINSTALL10v1}/modlib/resgrp.lib
rdresgr_266_> Number of residue groups:        2
openf___224_> Open           ${MODINSTALL10v1}/modlib/sstruc.lib

Dynamically allocated memory at   amaxlibraries [B,KiB,MiB]:      1196744    1168.695     1.141

Dynamically allocated memory at   amaxlibraries [B,KiB,MiB]:      1197272    1169.211     1.142
openf___224_> Open           ${MODINSTALL10v1}/modlib/resdih.lib

Dynamically allocated memory at   amaxlibraries [B,KiB,MiB]:      1245872    1216.672     1.188
rdrdih__263_> Number of dihedral angle types         :        9
              Maximal number of dihedral angle optima:        3
              Dihedral angle names                   :  Alph Phi Psi Omeg chi1 chi2 chi3 chi4 chi5
openf___224_> Open           ${MODINSTALL10v1}/modlib/radii.lib

Dynamically allocated memory at   amaxlibraries [B,KiB,MiB]:      1259172    1229.660     1.201
openf___224_> Open           $

openf___224_> Open           ${MODINSTALL10v1}/modlib/mnch3.lib
openf___224_> Open           ${MODINSTALL10v1}/modlib/xs4.mat
rdrrwgh_268_> Number of residue types:       21
openf___224_> Open           $(LIB)/top_heav.lib
read_to_681_> topology.submodel read from topology file:        3
openf___224_> Open           $(LIB)/par.lib

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1380604    1348.246     1.317

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1382204    1349.809     1.318

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1386184    1353.695     1.322

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1388184    1355.648     1.324

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1391184    1358.578     1.327

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1395684    1362.973     1.331

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1401256    1368.41

openf___224_> Open           ${MODINSTALL10v1}/modlib/mnch3.lib
openf___224_> Open           ${MODINSTALL10v1}/modlib/xs4.mat
rdrrwgh_268_> Number of residue types:       21
openf___224_> Open           $(LIB)/top_heav.lib
read_to_681_> topology.submodel read from topology file:        3
openf___224_> Open           $(LIB)/par.lib

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1378972    1346.652     1.315

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1380572    1348.215     1.317

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1384552    1352.102     1.320

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1386552    1354.055     1.322

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1389552    1356.984     1.325

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1394052    1361.379     1.329

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1399624    1366.82



>> ENERGY; Differences between the model's features and restraints:
Number of all residues in MODEL                   :       16
Number of all, selected real atoms                :      123       6
Number of all, selected pseudo atoms              :        0       0
Number of all static, selected restraints         :      616      42
COVALENT_CYS                                      :        F
NONBONDED_SEL_ATOMS                               :        1
Number of non-bonded pairs (excluding 1-2,1-3,1-4):       14
Dynamic pairs routine                             : 5, NATM_SEL x NATM double loop
Atomic shift for contacts update (UPDATE_DYNAMIC) :    0.390
LENNARD_JONES_SWITCH                              :    6.500   7.500
COULOMB_JONES_SWITCH                              :    6.500   7.500
RESIDUE_SPAN_RANGE                                :        0   99999
NLOGN_USE                                         :       15
CONTACT_SHELL                                     :    4.000
DYNAMI

openf___224_> Open           $(LIB)/par.lib

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1377308    1345.027     1.314

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1378908    1346.590     1.315

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1382888    1350.477     1.319

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1384888    1352.430     1.321

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1387888    1355.359     1.324

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1392388    1359.754     1.328

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1397960    1365.195     1.333

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1400760    1367.930     1.336

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1404960    1372.031     1.340

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1411260    1378.

...



>> ENERGY; Differences between the model's features and restraints:
Number of all residues in MODEL                   :       19
Number of all, selected real atoms                :      149      11
Number of all, selected pseudo atoms              :        0       0
Number of all static, selected restraints         :      747      61
COVALENT_CYS                                      :        F
NONBONDED_SEL_ATOMS                               :        1
Number of non-bonded pairs (excluding 1-2,1-3,1-4):       60
Dynamic pairs routine                             : 5, NATM_SEL x NATM double loop
Atomic shift for contacts update (UPDATE_DYNAMIC) :    0.390
LENNARD_JONES_SWITCH                              :    6.500   7.500
COULOMB_JONES_SWITCH                              :    6.500   7.500
RESIDUE_SPAN_RANGE                                :        0   99999
NLOGN_USE                                         :       15
CONTACT_SHELL                                     :    4.000
DYNAMI

openf___224_> Open           $(LIB)/par.lib

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1392968    1360.320     1.328

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1394568    1361.883     1.330

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1398548    1365.770     1.334

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1400548    1367.723     1.336

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1403548    1370.652     1.339

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1408048    1375.047     1.343

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1413620    1380.488     1.348

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1416420    1383.223     1.351

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1420620    1387.324     1.355

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1426920    1393.

openf___224_> Open           ${MODINSTALL10v1}/modlib/mnch3.lib
openf___224_> Open           ${MODINSTALL10v1}/modlib/xs4.mat
rdrrwgh_268_> Number of residue types:       21
openf___224_> Open           $(LIB)/top_heav.lib
read_to_681_> topology.submodel read from topology file:        3
openf___224_> Open           $(LIB)/par.lib

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1398322    1365.549     1.334

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1399922    1367.111     1.335

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1403902    1370.998     1.339

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1405902    1372.951     1.341

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1408902    1375.881     1.344

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1413402    1380.275     1.348

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1418974    1385.71

openf___224_> Open           ${MODINSTALL10v1}/modlib/mnch3.lib
openf___224_> Open           ${MODINSTALL10v1}/modlib/xs4.mat
rdrrwgh_268_> Number of residue types:       21
openf___224_> Open           $(LIB)/top_heav.lib
read_to_681_> topology.submodel read from topology file:        3
openf___224_> Open           $(LIB)/par.lib

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1397200    1364.453     1.332

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1398800    1366.016     1.334

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1402780    1369.902     1.338

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1404780    1371.855     1.340

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1407780    1374.785     1.343

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1412280    1379.180     1.347

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1417852    1384.62

openf___224_> Open           ${MODINSTALL10v1}/modlib/mnch3.lib
openf___224_> Open           ${MODINSTALL10v1}/modlib/xs4.mat
rdrrwgh_268_> Number of residue types:       21
openf___224_> Open           $(LIB)/top_heav.lib
read_to_681_> topology.submodel read from topology file:        3
openf___224_> Open           $(LIB)/par.lib

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1397550    1364.795     1.333

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1399150    1366.357     1.334

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1403130    1370.244     1.338

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1405130    1372.197     1.340

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1408130    1375.127     1.343

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1412630    1379.521     1.347

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      1418202    1384.96